In [1]:
# Imports you'll need.
from collections import Counter
import ConfigParser
import matplotlib.pyplot as plt
import networkx as nx
import sys
import time
from TwitterAPI import TwitterAPI

%matplotlib inline

In [2]:
#This method is done for you. Make sure to put your credentials in twitter.cfg.
def get_twitter(config_file):
    """ Read the config_file and construct an instance of TwitterAPI.
    Args:
      config_file ... A config file in ConfigParser format with Twitter credentials
    Returns:
      An instance of TwitterAPI.
    """
    config = ConfigParser.ConfigParser()
    config.read(config_file)
    twitter = TwitterAPI(
                   config.get('twitter', 'consumer_key'),
                   config.get('twitter', 'consumer_secret'),
                   config.get('twitter', 'access_token'),
                   config.get('twitter', 'access_token_secret'))
    return twitter

twitter = get_twitter('twitter.cfg')
print('Established Twitter connection.')

Established Twitter connection.


In [5]:
def read_candidates(filename):
    """ Read a list of usernames for U.S. presedential candidates
    Args:
      filename: The name of the text file containing in format:
         <twitter handle> <R or D for Republican or Democrat>
    Returns:
      A list of (string, string) tuples representing each (handle, party) pair.
    """
    # TODO
    candidate_file = open("candidates.txt", "r")
    candidate_temp1 = []
    candidate_temp1 =  candidate_file.read().splitlines()
    candidate_temp2 = []
    for x in range(len(candidate_temp1)):
             candidate_temp2.append(candidate_temp1[x].split())
    candidate_list = []
    for i in range(len(candidate_temp2)):
        x = candidate_temp2[i][0]
        y = candidate_temp2[i][1]
        candidate_list.append((x,y))
    candidate_file.close()
    return candidate_list
candidates = read_candidates('candidates.txt')
print('Read %d candidates' % len(candidates))
print('\n'.join(str(x) for x in candidates))

Read 15 candidates
('HillaryClinton', 'D')
('BernieSanders', 'D')
('MartinOMalley', 'D')
('JoeBiden', 'D')
('JimWebbUSA', 'D')
('realDonaldTrump', 'R')
('JebBush', 'R')
('RealBenCarson', 'R')
('marcorubio', 'R')
('ScottWalker', 'R')
('tedcruz', 'R')
('CarlyFiorina', 'R')
('GovMikeHuckabee', 'R')
('govchristie', 'R')
('DrRandPaul', 'R')


In [6]:
# separate candidates by party.
republicans = [c[0] for c in candidates if c[1] == 'R']
democrats = [c[0] for c in candidates if c[1] == 'D']
print('%d republicans, %d democrats' % (len(republicans), len(democrats)))

10 republicans, 5 democrats


In [16]:
# I've provided the method below to handle Twitter's rate limiting.
def robust_request(twitter, resource, params, max_tries=5):
    """ If a Twitter request fails, sleep for 15 minutes.
    Do this at most max_tries times before quitting.
    Args:
      twitter .... A TwitterAPI object.
      resource ... A resource string to request.
      params ..... A parameter dictionary for the request.
      max_tries .. The maximum number of tries to attempt.
    Returns:
      A TwitterResponse object, or None if failed.
    """
    for i in range(max_tries):
        request = twitter.request(resource, params)
        if request.status_code == 200:
            return request
        else:
            print >> sys.stderr, 'Got error:', request.text, '\nsleeping for 15 minutes.'
            sys.stderr.flush()
            time.sleep(61 * 15)

In [18]:
def get_friends(screen_name):
    """ Return a list of the users that this person follows on Twitter, up to 200.
    See https://dev.twitter.com/rest/reference/get/friends/list 
    Note, because of rate limits, it's best to test this method for one candidate before trying
    on all candidates.
    
    Args:
        screen_name: a string of a Twitter screen name
    Returns:
        A list of strings, one per friend.
    Note: Many users follow more than 200 accounts; we will limit ourselves to
    the first 200 accounts returned.
    """
    # TODO
    #Using the example request on the dev.twitter.com
    friend_list_dictionary = robust_request(twitter,'friends/list',{'screen_name' : screen_name, 'count':200})
    friend_follow = [i for i in friend_list_dictionary]
    #print friend_follow
    return friend_follow




[{u'follow_request_sent': False, u'has_extended_profile': False, u'profile_use_background_image': False, u'default_profile_image': False, u'id': 14125897, u'profile_background_image_url_https': u'https://pbs.twimg.com/profile_background_images/70582568/NH_Entering.jpg', u'verified': True, u'blocked_by': False, u'profile_text_color': u'000000', u'muting': False, u'profile_image_url_https': u'https://pbs.twimg.com/profile_images/529258423565565952/2uP67NKz_normal.jpeg', u'profile_sidebar_fill_color': u'FAF8CB', u'entities': {u'url': {u'urls': [{u'url': u'http://t.co/5XyW6PDSLP', u'indices': [0, 22], u'expanded_url': u'http://vote.jeanneshaheen.org', u'display_url': u'vote.jeanneshaheen.org'}]}, u'description': {u'urls': []}}, u'followers_count': 8584, u'profile_sidebar_border_color': u'FFFFFF', u'id_str': u'14125897', u'profile_background_color': u'00713D', u'listed_count': 634, u'status': {u'contributors': None, u'truncated': False, u'text': u'Today, I officially endorsed @HillaryClinto

In [14]:
def get_all_friends(screen_names):
    """ Get the friends for all the users in usernames.
    I.e., call get_friends for all 15 candidates.
    Args:
        screen_names: a list of Twitter screen names, one per candidate
    Returns:
        a dict mapping each candidate's username (string) to a list of his/her friends (strings)
    """
    return {n: get_friends(n) for n in screen_names}
candidate2friends = get_all_friends(c[0] for c in candidates)

TwitterRequestError: Twitter request failed (429)

[{u'follow_request_sent': False, u'has_extended_profile': False, u'profile_use_background_image': False, u'default_profile_image': False, u'id': 14125897, u'profile_background_image_url_https': u'https://pbs.twimg.com/profile_background_images/70582568/NH_Entering.jpg', u'verified': True, u'blocked_by': False, u'profile_text_color': u'000000', u'muting': False, u'profile_image_url_https': u'https://pbs.twimg.com/profile_images/529258423565565952/2uP67NKz_normal.jpeg', u'profile_sidebar_fill_color': u'FAF8CB', u'entities': {u'url': {u'urls': [{u'url': u'http://t.co/5XyW6PDSLP', u'indices': [0, 22], u'expanded_url': u'http://vote.jeanneshaheen.org', u'display_url': u'vote.jeanneshaheen.org'}]}, u'description': {u'urls': []}}, u'followers_count': 8582, u'profile_sidebar_border_color': u'FFFFFF', u'id_str': u'14125897', u'profile_background_color': u'00713D', u'listed_count': 634, u'status': {u'contributors': None, u'truncated': False, u'text': u'Today, I officially endorsed @HillaryClinto

TwitterRequestError: Twitter request failed (429)

In [15]:
# Print the number of friends per candidate, sorted by candidate name.
def print_num_friends(candidate2friends):
    # TODO
    for i in sorted(candidate2friends):
        x = len(candidate2friends[i])
        print "%s %d" %(i,x)
print_num_friends(candidate2friends)

NameError: name 'candidate2friends' is not defined